In [1]:
import scripts.stock_plots as stock_plots
import scripts.stock_analysis as stock_ana
import plotly.graph_objects as go

from datetime import datetime, timedelta
import pandas as pd
import numpy as np
import yfinance as yf

import requests
from bs4 import BeautifulSoup

pd.set_option("mode.chained_assignment", None)  # Ignore the warning

In [2]:
url = "https://www.tradingview.com/markets/stocks-usa/market-movers-active/"
response = requests.get(url)
soup = BeautifulSoup(response.content, "html.parser")

response = requests.get(url)
soup = BeautifulSoup(response.content, "html.parser")
table = soup.find("table")


In [3]:
data = pd.DataFrame(columns=["Ticker", "Vol*Price (M)", "Market cap (M)", "change"])


if response.status_code == 200:
    # Parse the HTML content of the webpage
    soup = BeautifulSoup(response.content, "html.parser")

    # Find the table element on the webpage (you need to inspect the webpage to find the specific HTML tags)
    table = soup.find("table")  # Example: finding the first table on the page

    # Check if the table element was found
    if table:
        # Extract the table rows
        rows = table.find_all("tr")

        # Loop through each row and extract the data
        for row in rows:

            ticker_cell = row.find("td", class_="cell-RLhfr_y4")
            if ticker_cell:
              ticker_symbol = ticker_cell.find("a", class_="tickerName-GrtoTeat").text.strip()
              # print(ticker_symbol)


              value_1_cell = row.find_all("td")[1]
              chg_cell = row.find_all("td")[3]
              value_2_cell = row.find_all("td")[6]

              value_1 = value_1_cell.text.strip().split()
              chg_val = chg_cell.text.strip()
              value_2 = value_2_cell.text.strip().split()


              if len(value_1) == len(value_2):
                def to_million(extract):
                  if extract[1] == "T":
                    return float(extract[0]) * 1e6
                  elif extract[1] == "B":
                    return float(extract[0]) * 1e3
                  else:
                    return float(extract[0])

                vol_price = to_million(value_1)
                market_cap = to_million(value_2)


                if chg_val[0] == "+":
                  chg = float(chg_val[1:-1])
                else:
                  chg = -float(chg_val[1:-1])

                if market_cap < 2000:
                  pass
                else:
                  # print(vol_price, market_cap, relative_active)
                  data.loc[len(data.index)] = [ticker_symbol, vol_price, market_cap, chg]


                  # data = data.append({"Ticker": ticker_symbol, "Vol*Price (M)": vol_price, "Market cap (M)": market_cap, "relative_active": relative_active}, ignore_index=True)
                  # data = pd.concat([ticker_symbol, vol_price, market_cap, relative_active], ignore_index=True)

    else:
        print("Table element not found on the webpage.")
else:
    print("Failed to retrieve webpage. Status code:", response.status_code)

In [4]:
data["rel_active"] = data["Vol*Price (M)"] / data["Market cap (M)"] * (abs(data["change"]))
data["rel_active(sqrt)"] = data["Vol*Price (M)"] / np.sqrt(data["Market cap (M)"]) * (abs(data["change"]))
data["rel_active(log)"] = data["Vol*Price (M)"] / np.log(data["Market cap (M)"]) * (abs(data["change"]))


data["rel_active() rank"] = data["rel_active"].rank(ascending=False)
data["rel_active(sqrt) rank"] = data["rel_active(sqrt)"].rank(ascending=False)
data["rel_active(log) rank"] = data["rel_active(log)"].rank(ascending=False)

data["rel_rank"] = data["rel_active() rank"]**2 + data["rel_active(sqrt) rank"]**2 + data["rel_active(log) rank"]**2
data["rel_active(rel_rank) rank"] = data["rel_rank"].rank()


In [5]:
data.sort_values(by="rel_active(rel_rank) rank").head(10)

Ticker  Vol*Price (M)  Market cap (M)  change  rel_active  \
12   MSTR       2656.000         18072.0  -17.63    2.591040   
1    TSLA      23282.000        584516.0   -5.55    0.221063   
7    SMCI       6329.000         50283.0   -3.54    0.445571   
43   GEHC       1100.000         34716.0  -14.28    0.452471   
16   COIN       1861.000         50241.0   -6.52    0.241510   
94   MARA        675.835          4539.0  -10.93    1.627424   
47    MPC       1051.000         65480.0   -9.37    0.150395   
22    MMM       1615.000         53405.0    4.72    0.142736   
8     LLY       5809.000        742643.0    5.95    0.046541   
79   PCAR        783.109         55603.0   -6.63    0.093376   

    rel_active(sqrt)  rel_active(log)  rel_active() rank  \
12        348.319088      4777.056851                1.0   
1         169.011037      9731.122963                6.0   
7          99.914327      2069.633805                4.0   
43         84.305528      1502.445354                3.0   
16         54.133341      1120.940719                5.0   
94        109.642960       877.253118                2.0   
47         38.484688       888.035527                7.0   
22         32.985538       700.260732                8.0   
8          40.107750      2556.859362               23.0   
79         22.018444       475.198267               11.0   

    rel_active(sqrt) rank  rel_active(log) rank  rel_rank  \
12                    1.0                   2.0       6.0   
1                     2.0                   1.0      41.0   
7                     4.0                   7.0      81.0   
43                    5.0                   8.0      98.0   
16                    6.0                  10.0     161.0   
94                    3.0                  13.0     182.0   
47                    9.0                  11.0     251.0   
22                   10.0                  14.0     360.0   
8                     8.0                   5.0     618.0   
79                   12.0                  19.0     626.0   

    rel_active(rel_rank) rank  
12                        1.0  
1                         2.0  
7                         3.0  
43                        4.0  
16                        5.0  
94                        6.0  
47                        7.0  
22                        8.0  
8                         9.0  
79                       10.0

In [6]:
def download_data(stocks):
    stocks_str = " ".join(stocks)
    return yf.Tickers(stocks_str)

In [9]:
selected_tickers = data.sort_values(by="rel_active(rel_rank) rank")["Ticker"].head(50).values

stock_data = download_data(selected_tickers)



for ticker in selected_tickers:
    stock_plot = stock_plots.PlotInfo(stock_data.tickers[ticker], ticker, "150d")
    try:
        candle = stock_plot.generate_recent_candles(p2p_order=4, days=50)
        # candle = stock_plot.generate_candle_plot(p2p_order=4)
        candle.show()
    except:
        pass